<a href="https://colab.research.google.com/github/hasanzeynal/Machine-Learning/blob/main/classification/02%20-%20lazy_classifier.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
#importing libraries
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px
import seaborn as sns

from sklearn.preprocessing import OneHotEncoder,LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import RobustScaler

from ydata_profiling import ProfileReport
import lazypredict
from lazypredict.Supervised import LazyClassifier

import time
import warnings
warnings.filterwarnings('ignore')

In [ ]:
#pip install lazypredict

In [ ]:
#pip install ydata_profiling

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
df = pd.read_csv('/content/drive/MyDrive/datasets/Hotel Reservations.csv')
df.head()

Booking_ID  no_of_adults  no_of_children  no_of_weekend_nights  \
0   INN00001             2               0                     1   
1   INN00002             2               0                     2   
2   INN00003             1               0                     2   
3   INN00004             2               0                     0   
4   INN00005             2               0                     1   

   no_of_week_nights type_of_meal_plan  required_car_parking_space  \
0                  2       Meal Plan 1                           0   
1                  3      Not Selected                           0   
2                  1       Meal Plan 1                           0   
3                  2       Meal Plan 1                           0   
4                  1      Not Selected                           0   

  room_type_reserved  lead_time  arrival_year  arrival_month  arrival_date  \
0        Room_Type 1        224          2017             10             2   
1        Room_Type 1          5          2018             11             6   
2        Room_Type 1          1          2018              2            28   
3        Room_Type 1        211          2018              5            20   
4        Room_Type 1         48          2018              4            11   

  market_segment_type  repeated_guest  no_of_previous_cancellations  \
0             Offline               0                             0   
1              Online               0                             0   
2              Online               0                             0   
3              Online               0                             0   
4              Online               0                             0   

   no_of_previous_bookings_not_canceled  avg_price_per_room  \
0                                     0               65.00   
1                                     0              106.68   
2                                     0               60.00   
3                                     0              100.00   
4                                     0               94.50   

   no_of_special_requests booking_status  
0                       0   Not_Canceled  
1                       1   Not_Canceled  
2                       0       Canceled  
3                       0       Canceled  
4                       0       Canceled

# Data Preperation and Understanting

In [ ]:
df.columns

Index(['Booking_ID', 'no_of_adults', 'no_of_children', 'no_of_weekend_nights',
       'no_of_week_nights', 'type_of_meal_plan', 'required_car_parking_space',
       'room_type_reserved', 'lead_time', 'arrival_year', 'arrival_month',
       'arrival_date', 'market_segment_type', 'repeated_guest',
       'no_of_previous_cancellations', 'no_of_previous_bookings_not_canceled',
       'avg_price_per_room', 'no_of_special_requests', 'booking_status'],
      dtype='object')

In [ ]:
df.describe().T

count    mean   std     min     25%  \
no_of_adults                         36275.00    1.84  0.52    0.00    2.00   
no_of_children                       36275.00    0.11  0.40    0.00    0.00   
no_of_weekend_nights                 36275.00    0.81  0.87    0.00    0.00   
no_of_week_nights                    36275.00    2.20  1.41    0.00    1.00   
required_car_parking_space           36275.00    0.03  0.17    0.00    0.00   
lead_time                            36275.00   85.23 85.93    0.00   17.00   
arrival_year                         36275.00 2017.82  0.38 2017.00 2018.00   
arrival_month                        36275.00    7.42  3.07    1.00    5.00   
arrival_date                         36275.00   15.60  8.74    1.00    8.00   
repeated_guest                       36275.00    0.03  0.16    0.00    0.00   
no_of_previous_cancellations         36275.00    0.02  0.37    0.00    0.00   
no_of_previous_bookings_not_canceled 36275.00    0.15  1.75    0.00    0.00   
avg_price_per_room                   36275.00  103.42 35.09    0.00   80.30   
no_of_special_requests               36275.00    0.62  0.79    0.00    0.00   

                                         50%     75%     max  
no_of_adults                            2.00    2.00    4.00  
no_of_children                          0.00    0.00   10.00  
no_of_weekend_nights                    1.00    2.00    7.00  
no_of_week_nights                       2.00    3.00   17.00  
required_car_parking_space              0.00    0.00    1.00  
lead_time                              57.00  126.00  443.00  
arrival_year                         2018.00 2018.00 2018.00  
arrival_month                           8.00   10.00   12.00  
arrival_date                           16.00   23.00   31.00  
repeated_guest                          0.00    0.00    1.00  
no_of_previous_cancellations            0.00    0.00   13.00  
no_of_previous_bookings_not_canceled    0.00    0.00   58.00  
avg_price_per_room                     99.45  120.00  540.00  
no_of_special_requests                  0.00    1.00    5.00

In [ ]:
df.describe(include='object').T

count unique           top   freq
Booking_ID           36275  36275      INN00001      1
type_of_meal_plan    36275      4   Meal Plan 1  27835
room_type_reserved   36275      7   Room_Type 1  28130
market_segment_type  36275      5        Online  23214
booking_status       36275      2  Not_Canceled  24390

## Profile Report

In [ ]:
ProfileReport(df,title='Report about data',dark_mode=True)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
#booking_id is a unique value,so let's get delete it
df.drop('Booking_ID',axis=1,inplace=True)

In [ ]:
#value counts of object features to see which encoder method we need
for cols in df.columns:
    if df[cols].dtype =='object':
        print(f"{df[cols].value_counts()}")

Meal Plan 1     27835
Not Selected     5130
Meal Plan 2      3305
Meal Plan 3         5
Name: type_of_meal_plan, dtype: int64
Room_Type 1    28130
Room_Type 4     6057
Room_Type 6      966
Room_Type 2      692
Room_Type 5      265
Room_Type 7      158
Room_Type 3        7
Name: room_type_reserved, dtype: int64
Online           23214
Offline          10528
Corporate         2017
Complementary      391
Aviation           125
Name: market_segment_type, dtype: int64
Not_Canceled    24390
Canceled        11885
Name: booking_status, dtype: int64


In [ ]:
#one hot encoding would be preferable because it creates a new binary column for each category in the variable
#converting type of columns
df['type_of_meal_plan'] = df['type_of_meal_plan'].astype('category')
df['room_type_reserved'] = df['room_type_reserved'].astype('category')
df['market_segment_type'] = df['market_segment_type'].astype('category')
df['booking_status'] = df['booking_status'].astype('category')
#assign them to another columns
df['new_type_of_meal_plan'] = df['type_of_meal_plan'].cat.codes
df['new_room_type_reserved'] = df['room_type_reserved'].cat.codes
df['new_market_segment_type'] = df['market_segment_type'].cat.codes
df['newbooking_status'] = df['market_segment_type'].cat.codes
#creating one hot encoding and get dummies
ohe = OneHotEncoder()
one_hot_encoded_data = pd.get_dummies(df, columns = ['type_of_meal_plan', 'room_type_reserved','market_segment_type','booking_status'])
enc_data=pd.DataFrame(ohe.fit_transform(df[['new_type_of_meal_plan', 'new_room_type_reserved','new_market_segment_type','newbooking_status']]).toarray())
new_data = enc_data.join(df)

In [ ]:
new_data.drop([1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20],axis=1,inplace=True)

In [ ]:
new_data.drop([0,'type_of_meal_plan','room_type_reserved','booking_status','market_segment_type'],axis=1,inplace=True)

In [ ]:
new_data

no_of_adults  no_of_children  no_of_weekend_nights  no_of_week_nights  \
0                 2               0                     1                  2   
1                 2               0                     2                  3   
2                 1               0                     2                  1   
3                 2               0                     0                  2   
4                 2               0                     1                  1   
...             ...             ...                   ...                ...   
36270             3               0                     2                  6   
36271             2               0                     1                  3   
36272             2               0                     2                  6   
36273             2               0                     0                  3   
36274             2               0                     1                  2   

       required_car_parking_space  lead_time  arrival_year  arrival_month  \
0                               0        224          2017             10   
1                               0          5          2018             11   
2                               0          1          2018              2   
3                               0        211          2018              5   
4                               0         48          2018              4   
...                           ...        ...           ...            ...   
36270                           0         85          2018              8   
36271                           0        228          2018             10   
36272                           0        148          2018              7   
36273                           0         63          2018              4   
36274                           0        207          2018             12   

       arrival_date  repeated_guest  no_of_previous_cancellations  \
0                 2               0                             0   
1                 6               0                             0   
2                28               0                             0   
3                20               0                             0   
4                11               0                             0   
...             ...             ...                           ...   
36270             3               0                             0   
36271            17               0                             0   
36272             1               0                             0   
36273            21               0                             0   
36274            30               0                             0   

       no_of_previous_bookings_not_canceled  avg_price_per_room  \
0                                         0               65.00   
1                                         0              106.68   
2                                         0               60.00   
3                                         0              100.00   
4                                         0               94.50   
...                                     ...                 ...   
36270                                     0              167.80   
36271                                     0               90.95   
36272                                     0               98.39   
36273                                     0               94.50   
36274                                     0              161.67   

       no_of_special_requests  new_type_of_meal_plan  new_room_type_reserved  \
0                           0                      0                       0   
1                           1                      3                       0   
2                           0                      0                       0   
3                           0                      0                       0   
4                           0                      3                       0   
...    

In [ ]:
new_data.corr()['newbooking_status']

no_of_adults                            0.31
no_of_children                          0.13
no_of_weekend_nights                    0.13
no_of_week_nights                       0.11
required_car_parking_space             -0.00
lead_time                              -0.01
arrival_year                            0.15
arrival_month                          -0.01
arrival_date                            0.01
repeated_guest                         -0.34
no_of_previous_cancellations           -0.07
no_of_previous_bookings_not_canceled   -0.21
avg_price_per_room                      0.38
no_of_special_requests                  0.31
new_type_of_meal_plan                   0.20
new_room_type_reserved                  0.16
new_market_segment_type                 1.00
newbooking_status                       1.00
Name: newbooking_status, dtype: float64

In [ ]:
#via the correlation,there is no need new_market_segment_type,
#it is the same thing with our target value(booking status),it can be caused multicollinearity
new_data.drop('new_market_segment_type',axis=1,inplace=True)
#required_car_parking_space,lead_time,arrival_month,arrival_date can be deleted because of the correlation score(0.05)
new_data.drop(['required_car_parking_space','lead_time','arrival_month','arrival_date'],axis=1,inplace=True)

In [ ]:
new_data.head()

no_of_adults  no_of_children  no_of_weekend_nights  no_of_week_nights  \
0             2               0                     1                  2   
1             2               0                     2                  3   
2             1               0                     2                  1   
3             2               0                     0                  2   
4             2               0                     1                  1   

   arrival_year  repeated_guest  no_of_previous_cancellations  \
0          2017               0                             0   
1          2018               0                             0   
2          2018               0                             0   
3          2018               0                             0   
4          2018               0                             0   

   no_of_previous_bookings_not_canceled  avg_price_per_room  \
0                                     0               65.00   
1                                     0              106.68   
2                                     0               60.00   
3                                     0              100.00   
4                                     0               94.50   

   no_of_special_requests  new_type_of_meal_plan  new_room_type_reserved  \
0                       0                      0                       0   
1                       1                      3                       0   
2                       0                      0                       0   
3                       0                      0                       0   
4                       0                      3                       0   

   newbooking_status  
0                  3  
1                  4  
2                  4  
3                  4  
4                  4

In [ ]:
#implementing target and intepented features
X = new_data.drop('newbooking_status',axis=1)
y = new_data['newbooking_status']
#train test splitting
X_train,X_test,y_train,y_test = train_test_split(X,y,test_size=0.2,random_state=42)

In [ ]:
#feature scalling on the all intepented features(X)
rs = RobustScaler()
X = rs.fit_transform(X)

# Modelling


## Modelling with KNN

In [ ]:
#modelling with the K_Nearest Neighbours to see average accuracy score,then we will create LazyClassifier
from sklearn.neighbors import KNeighborsClassifier
knn = KNeighborsClassifier(n_neighbors=10)
knn.fit(X_train,y_train)
knn_predicts = knn.predict(X_test)
from sklearn.metrics import accuracy_score
accuracy_score(knn_predicts,y_test)

0.8656099241902137

In [ ]:
#we should change the scikit-learn version to the 0.23.1 because LazyLearner is not supported in the other versions
#when we use jupyter notebook,google colab must be way much great 

#pip3 uninstall scikit-learn -y
#pip install scikit-learn==0.23.1

## Modelling with  the Lazy Classifier

In [ ]:
#Selectig initial 10 classifiers
lazypredict.Supervised.CLASSIFIERS = lazypredict.Supervised.CLASSIFIERS[:10]
lazypredict.Supervised.CLASSIFIERS

[('AdaBoostClassifier', sklearn.ensemble._weight_boosting.AdaBoostClassifier),
 ('BaggingClassifier', sklearn.ensemble._bagging.BaggingClassifier),
 ('BernoulliNB', sklearn.naive_bayes.BernoulliNB),
 ('CalibratedClassifierCV', sklearn.calibration.CalibratedClassifierCV),
 ('CategoricalNB', sklearn.naive_bayes.CategoricalNB),
 ('DecisionTreeClassifier', sklearn.tree._classes.DecisionTreeClassifier),
 ('DummyClassifier', sklearn.dummy.DummyClassifier),
 ('ExtraTreeClassifier', sklearn.tree._classes.ExtraTreeClassifier),
 ('ExtraTreesClassifier', sklearn.ensemble._forest.ExtraTreesClassifier),
 ('GaussianNB', sklearn.naive_bayes.GaussianNB)]

In [ ]:
# fit selected models
clf = LazyClassifier(verbose=0,ignore_warnings=True, custom_metric=None)
models,predictions = clf.fit(X_train, X_test, y_train, y_test)
models


100%|██████████| 10/10 [00:55<00:00,  5.56s/it]


Accuracy  Balanced Accuracy ROC AUC  F1 Score  \
Model                                                                   
BaggingClassifier           0.90               0.82    None      0.90   
DecisionTreeClassifier      0.90               0.81    None      0.90   
ExtraTreesClassifier        0.89               0.80    None      0.89   
ExtraTreeClassifier         0.89               0.76    None      0.89   
GaussianNB                  0.64               0.56    None      0.68   
CalibratedClassifierCV      0.75               0.44    None      0.75   
AdaBoostClassifier          0.70               0.43    None      0.68   
BernoulliNB                 0.72               0.38    None      0.71   
DummyClassifier             0.64               0.20    None      0.50   

                        Time Taken  
Model                               
BaggingClassifier             0.81  
DecisionTreeClassifier        0.16  
ExtraTreesClassifier          2.81  
ExtraTreeClassifier           0.08  
GaussianNB                    0.05  
CalibratedClassifierCV       50.09  
AdaBoostClassifier            1.36  
BernoulliNB                   0.07  
DummyClassifier               0.05

In [ ]:
#Model is in the index,so if we wanna create some visualizations to show how good the models are,
#let's get changed them as a column
models = models.reset_index()
models.drop(['index','level_0'],axis=1,inplace=True)
models

Model  Accuracy  Balanced Accuracy ROC AUC  F1 Score  \
0       BaggingClassifier      0.90               0.82    None      0.90   
1  DecisionTreeClassifier      0.90               0.81    None      0.90   
2    ExtraTreesClassifier      0.89               0.80    None      0.89   
3     ExtraTreeClassifier      0.89               0.76    None      0.89   
4              GaussianNB      0.64               0.56    None      0.68   
5  CalibratedClassifierCV      0.75               0.44    None      0.75   
6      AdaBoostClassifier      0.70               0.43    None      0.68   
7             BernoulliNB      0.72               0.38    None      0.71   
8         DummyClassifier      0.64               0.20    None      0.50   

   Time Taken  
0        0.81  
1        0.16  
2        2.81  
3        0.08  
4        0.05  
5       50.09  
6        1.36  
7        0.07  
8        0.05

In [ ]:
#new_datadf = px.data.gapminder()
line = px.line(data_frame = models,x = 'Model',y = 'Accuracy')
line.update_traces(line_color ='red')
line.show()

In [ ]:
line = px.line(data_frame = models,y = ['Accuracy','F1 Score'])
line.show()

# Stradified K-Fold

In [ ]:
#stradifiedKFold in the best model(bagging classifier)
from sklearn.ensemble import BaggingClassifier
from sklearn.model_selection import StratifiedKFold
RF_scores = []
RF_fimp = []
RF_predictions = 0
FOLDS = 5
skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
#columns of X and y
features = []
target = ['newbooking_status']
for cols in new_data.columns:
  if cols == 'newbooking_status':
    break
  features.append(cols)

for fold, (train_idx, valid_idx) in enumerate(skf.split(df[features], df[target])):
    print(10*"=", f"Fold={fold+1}", 10*"=")
    start_time = time.time()
    
    X_train, X_test, y_train, y_test = train_test_split(X, y,
    test_size=0.2, shuffle = True, random_state = 8)

    # Use the same function above for the validation set
    X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, 
    test_size=0.25, random_state= 8) # 0.25 x 0.8 = 0.2

    #modelling
    model = BaggingClassifier()
    model.fit(X_train, y_train)

    #predictions
    preds_valid = model.predict(X_val)
    acc = accuracy_score(y_val,  preds_valid)
    RF_scores.append(acc)
    run_time = time.time() - start_time
    
    #printing folds,accuracy,run time
    print(f"Fold={fold+1}, Accuracy score: {100*acc:.2f}%, Run Time: {run_time:.2f}s")
    test_preds = model.predict(X_test) 
    RF_predictions += test_preds/FOLDS

print("")
print("Mean Accuracy :", np.mean(RF_scores))


========== Fold=1 ==========
Fold=1, Accuracy score: 89.35%, Run Time: 0.40s
========== Fold=2 ==========
Fold=2, Accuracy score: 89.55%, Run Time: 0.41s
========== Fold=3 ==========
Fold=3, Accuracy score: 89.40%, Run Time: 0.41s
========== Fold=4 ==========
Fold=4, Accuracy score: 89.81%, Run Time: 0.41s
========== Fold=5 ==========
Fold=5, Accuracy score: 89.52%, Run Time: 0.43s

Mean Accuracy : 0.8952722260509993
